In [1]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os
import pickle

In [5]:
# dict to convert ensembl id to symbol (doesn't really work :/)
with open('ensembl_to_genesymbol.pickle', 'rb') as handle:
    ensembl_to_genesymbol = pickle.load(handle)

In [2]:
# Combine all files into df 

directory = "counts"

df = pd.DataFrame()
df["ProbeID"] = 0

for filename in os.listdir(directory):
    f = os.path.join(directory, filename)
    gsmid = filename.split("_")[0]
    print("processing", gsmid)
    newdf = pd.DataFrame(pd.read_csv(directory+"/"+filename, sep = '\t', header=0))
    newdf.columns = ["ProbeID", gsmid]
    df["ProbeID"] = newdf["ProbeID"]
    df = df.merge(newdf, how="outer", on="ProbeID")
    
# Replace Ensembl IDs with gene names
ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Mus_musculus.GRCm38.94.txt", sep = '\t', header=None)) 
ensembl_df.columns = ["ProbeID", "Name"]
df = ensembl_df.merge(df, how="outer",on="ProbeID")

df.drop(df.index[55359:55364], inplace=True)
df.replace(to_replace=math.nan, value=0, inplace=True) # Deal with missing values
df["Name"] = [i if i != 0 else "" for i in df["Name"]]
df

processing GSM5696212
processing GSM5696205
processing GSM5696214
processing GSM5696216
processing GSM5696215
processing GSM5696201
processing GSM5696211
processing GSM5696209
processing GSM5696208
processing GSM5696206
processing GSM5696210
processing GSM5696204
processing GSM5696203
processing GSM5696200
processing GSM5696199
processing GSM5696213
processing GSM5696202
processing GSM5696207


ProbeID           Name  GSM5696212  GSM5696205  GSM5696214  \
0      ENSMUSG00000102693  4933401J01Rik         0.0         1.0         0.0   
1      ENSMUSG00000064842        Gm26206         0.0         0.0         1.0   
2      ENSMUSG00000051951           Xkr4         0.0         0.0         0.0   
3      ENSMUSG00000102851        Gm18956         2.0         0.0         0.0   
4      ENSMUSG00000103377        Gm37180         0.0         0.0         0.0   
...                   ...            ...         ...         ...         ...   
55354  ENSMUSG00000116726                        0.0         0.0         0.0   
55355  ENSMUSG00000116787                        0.0         0.0         0.0   
55356  ENSMUSG00000116844                        0.0         0.0         0.0   
55357  ENSMUSG00000116856                        0.0         0.0         0.0   
55358  ENSMUSG00000116869                        0.0         0.0         0.0   

       GSM5696216  GSM5696215  GSM5696201  GSM5696211  GSM5696209  GSM5696208  \
0             0.0         0.0         0.0         0.0         0.0         0.0   
1             0.0         1.0         0.0         0.0         0.0         0.0   
2             0.0         0.0         0.0         0.0         0.0         0.0   
3             0.0         0.0         0.0         0.0         0.0         0.0   
4             0.0         0.0         0.0         0.0         0.0         0.0   
...           ...         ...         ...         ...         ...         ...   
55354         0.0         0.0         0.0         0.0         0.0         0.0   
55355         0.0         0.0         0.0         0.0         0.0         0.0   
55356         0.0         0.0         0.0         0.0         0.0         0.0   
55357         0.0         0.0         0.0         0.0         0.0         0.0   
55358         0.0         0.0         0.0         0.0         0.0         0.0   

       GSM5696206  GSM5696210  GSM5696204  GSM5696203  GSM5696200  GSM5696199  \
0             0.0         0.0         0.0         0.0         0.0         0.0   
1             0.0         0.0         0.0         0.0         0.0         0.0   
2             0.0         0.0         0.0         0.0         0.0         0.0   
3             0.0         0.0         0.0         0.0         0.0         0.0   
4             0.0         0.0         0.0         0.0         0.0         0.0   
...           ...         ...         ...         ...         ...         ...   
55354         0.0         0.0         0.0         0.0         0.0         0.0   
55355         0.0         0.0         0.0         0.0         0.0         0.0   
55356         0.0         0.0         0.0         0.0         0.0         0.0   
55357         0.0         0.0         0.0         0.0         0.0         0.0   
55358         0.0         0.0         0.0         0.0         0.0         0.0   

       GSM5696213  GSM5696202  GSM5696207  
0             0.0         0.0         0.0  
1             0.0         0.0         0.0  
2             1.0         0.0         0.0  
3             0.0         0.0         0.0  
4             0.0         0.0         0.0  
...           ...         ...         ...  
55354         0.0         0.0         0.0  
55355         0.0         0.0         0.0  
55356         0.0         0.0         0.0  
55357         0.0         0.0         0.0  
55358         0.0         0.0         0.0  

[55359 rows x 20 columns]

In [3]:
expr = df.copy(deep=True)
expr = expr.drop(['ProbeID', 'Name'], axis=1)

print("Taking log")
adata = sc.AnnData(expr.T)
sc.pp.normalize_total(adata, target_sum=1e6)
sc.pp.log1p(adata, base = 2)

expr = pd.DataFrame(adata.X)
expr = expr.T

genes = pd.DataFrame()
genes["ProbeID"] = df["ProbeID"]
genes["Name"] = df["Name"]
expr = pd.concat([genes, expr], axis=1)
expr.columns = df.columns

Taking log


/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


In [4]:
expr

ProbeID           Name  GSM5696212  GSM5696205  GSM5696214  \
0      ENSMUSG00000102693  4933401J01Rik     0.00000    0.620846    0.000000   
1      ENSMUSG00000064842        Gm26206     0.00000    0.000000    0.257322   
2      ENSMUSG00000051951           Xkr4     0.00000    0.000000    0.000000   
3      ENSMUSG00000102851        Gm18956     0.38795    0.000000    0.000000   
4      ENSMUSG00000103377        Gm37180     0.00000    0.000000    0.000000   
...                   ...            ...         ...         ...         ...   
55354  ENSMUSG00000116726                    0.00000    0.000000    0.000000   
55355  ENSMUSG00000116787                    0.00000    0.000000    0.000000   
55356  ENSMUSG00000116844                    0.00000    0.000000    0.000000   
55357  ENSMUSG00000116856                    0.00000    0.000000    0.000000   
55358  ENSMUSG00000116869                    0.00000    0.000000    0.000000   

       GSM5696216  GSM5696215  GSM5696201  GSM5696211  GSM5696209  GSM5696208  \
0             0.0    0.000000         0.0         0.0         0.0         0.0   
1             0.0    0.225538         0.0         0.0         0.0         0.0   
2             0.0    0.000000         0.0         0.0         0.0         0.0   
3             0.0    0.000000         0.0         0.0         0.0         0.0   
4             0.0    0.000000         0.0         0.0         0.0         0.0   
...           ...         ...         ...         ...         ...         ...   
55354         0.0    0.000000         0.0         0.0         0.0         0.0   
55355         0.0    0.000000         0.0         0.0         0.0         0.0   
55356         0.0    0.000000         0.0         0.0         0.0         0.0   
55357         0.0    0.000000         0.0         0.0         0.0         0.0   
55358         0.0    0.000000         0.0         0.0         0.0         0.0   

       GSM5696206  GSM5696210  GSM5696204  GSM5696203  GSM5696200  GSM5696199  \
0             0.0         0.0         0.0         0.0         0.0         0.0   
1             0.0         0.0         0.0         0.0         0.0         0.0   
2             0.0         0.0         0.0         0.0         0.0         0.0   
3             0.0         0.0         0.0         0.0         0.0         0.0   
4             0.0         0.0         0.0         0.0         0.0         0.0   
...           ...         ...         ...         ...         ...         ...   
55354         0.0         0.0         0.0         0.0         0.0         0.0   
55355         0.0         0.0         0.0         0.0         0.0         0.0   
55356         0.0         0.0         0.0         0.0         0.0         0.0   
55357         0.0         0.0         0.0         0.0         0.0         0.0   
55358         0.0         0.0         0.0         0.0         0.0         0.0   

       GSM5696213  GSM5696202  GSM5696207  
0        0.000000         0.0         0.0  
1        0.000000         0.0         0.0  
2        0.249577         0.0         0.0  
3        0.000000         0.0         0.0  
4        0.000000         0.0         0.0  
...           ...         ...         ...  
55354    0.000000         0.0         0.0  
55355    0.000000         0.0         0.0  
55356    0.000000         0.0         0.0  
55357    0.000000         0.0         0.0  
55358    0.000000         0.0         0.0  

[55359 rows x 20 columns]

In [5]:
# No. of missing gene names
names = list(expr["Name"])
names.count("")

827

In [6]:
path_dir = "./"
expr.to_csv(path_dir+"GSE189213-GPL21626-expr.txt", header=True, index=False,sep='\t')

In [7]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE189213-GPL21626-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE189213-GPL21626-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
